# Resistance/Support AND Candles Patterns

In [17]:
import pandas as pd
df = pd.read_csv("EURUSD_Candlestick_5_M_ASK_30_09_2019_30_09_2022.csv")

#Check if NA values are in data
df=df[df['Volume']!=0]
df.reset_index(drop=True, inplace=True)
df.isna().sum()
df.tail()

Gmt time     Open     High      Low    Close   Volume
225081  30.09.2022 20:35:00.000  0.98028  0.98034  0.98001  0.98022   624.12
225082  30.09.2022 20:40:00.000  0.98023  0.98047  0.98007  0.98030   408.20
225083  30.09.2022 20:45:00.000  0.98026  0.98034  0.98019  0.98031   317.29
225084  30.09.2022 20:50:00.000  0.98031  0.98067  0.97987  0.97999  1472.13
225085  30.09.2022 20:55:00.000  0.98000  0.98066  0.97993  0.98026  1068.81

# Support and Resistance FUNCTIONS

In [18]:
def support(df1, l, n1, n2): #n1 n2 before and after candle l
    for i in range(l-n1+1, l+1):
        if(df1.Low[i]>df1.Low[i-1]):
            return 0
    for i in range(l+1,l+n2+1):
        if(df1.Low[i]<df1.Low[i-1]):
            return 0
    return 1

def resistance(df1, l, n1, n2): #n1 n2 before and after candle l
    for i in range(l-n1+1, l+1):
        if(df1.High[i]<df1.High[i-1]):
            return 0
    for i in range(l+1,l+n2+1):
        if(df1.High[i]>df1.High[i-1]):
            return 0
    return 1

In [19]:
length = len(df)
High = list(df['High'])
Low = list(df['Low'])
Close = list(df['Close'])
Open = list(df['Open'])
bodydiff = [0] * length

highdiff = [0] * length
lowdiff = [0] * length
ratio1 = [0] * length
ratio2 = [0] * length

def isEngulfing(l):
    row=l
    bodydiff[row] = abs(Open[row]-Close[row])
    if bodydiff[row]<0.000001:
        bodydiff[row]=0.000001      

    bodydiffmin = 0.002
    if (bodydiff[row]>bodydiffmin and bodydiff[row-1]>bodydiffmin and
        Open[row-1]<Close[row-1] and
        Open[row]>Close[row] and 
        (Open[row]-Close[row-1])>=-0e-5 and Close[row]<Open[row-1]): #+0e-5 -5e-5
        return 1

    elif(bodydiff[row]>bodydiffmin and bodydiff[row-1]>bodydiffmin and
        Open[row-1]>Close[row-1] and
        Open[row]<Close[row] and 
        (Open[row]-Close[row-1])<=+0e-5 and Close[row]>Open[row-1]):#-0e-5 +5e-5
        return 2
    else:
        return 0
       
def isStar(l):
    bodydiffmin = 0.0020
    row=l
    highdiff[row] = High[row]-max(Open[row],Close[row])
    lowdiff[row] = min(Open[row],Close[row])-Low[row]
    bodydiff[row] = abs(Open[row]-Close[row])
    if bodydiff[row]<0.000001:
        bodydiff[row]=0.000001
    ratio1[row] = highdiff[row]/bodydiff[row]
    ratio2[row] = lowdiff[row]/bodydiff[row]

    if (ratio1[row]>1 and lowdiff[row]<0.2*highdiff[row] and bodydiff[row]>bodydiffmin):# and Open[row]>Close[row]):
        return 1
    elif (ratio2[row]>1 and highdiff[row]<0.2*lowdiff[row] and bodydiff[row]>bodydiffmin):# and Open[row]<Close[row]):
        return 2
    else:
        return 0
    
def closeResistance(l,levels,lim):
    if len(levels)==0:
        return 0
    c1 = abs(df.High[l]-min(levels, key=lambda x:abs(x-df.High[l])))<=lim
    c2 = abs(max(df.Open[l],df.Close[l])-min(levels, key=lambda x:abs(x-df.High[l])))<=lim
    c3 = min(df.Open[l],df.Close[l])<min(levels, key=lambda x:abs(x-df.High[l]))
    c4 = df.Low[l]<min(levels, key=lambda x:abs(x-df.High[l]))
    if( (c1 or c2) and c3 and c4 ):
        return 1
    else:
        return 0
    
def closeSupport(l,levels,lim):
    if len(levels)==0:
        return 0
    c1 = abs(df.Low[l]-min(levels, key=lambda x:abs(x-df.Low[l])))<=lim
    c2 = abs(min(df.Open[l],df.Close[l])-min(levels, key=lambda x:abs(x-df.Low[l])))<=lim
    c3 = max(df.Open[l],df.Close[l])>min(levels, key=lambda x:abs(x-df.Low[l]))
    c4 = df.High[l]>min(levels, key=lambda x:abs(x-df.Low[l]))
    if( (c1 or c2) and c3 and c4 ):
        return 1
    else:
        return 0

In [20]:
n1=2
n2=2
backCandles=30
signal = [0] * length

for row in range(backCandles, len(df)-n2):
    ss = []
    rr = []
    for subrow in range(row-backCandles+n1, row+1):
        if support(df, subrow, n1, n2):
            ss.append(df.Low[subrow])
        if resistance(df, subrow, n1, n2):
            rr.append(df.High[subrow])
    #!!!! parameters
    if ((isEngulfing(row)==1 or isStar(row)==1) and closeResistance(row, rr, 150e-5) ):#and df.RSI[row]<30
        signal[row] = 1
    elif((isEngulfing(row)==2 or isStar(row)==2) and closeSupport(row, ss, 150e-5)):#and df.RSI[row]>70
        signal[row] = 2
    else:
        signal[row] = 0



In [21]:
df['signal']=signal

In [22]:
df[df['signal']==2].count()

Gmt time    3
Open        3
High        3
Low         3
Close       3
Volume      3
signal      3
dtype: int64

In [ ]:
import pandas as pd
df = pd.read_csv("EURUSD_Candlestick_5_M_ASK_30_09_2019_30_09_2022.csv")

#Check if NA values are in data
df=df[df['Volume']!=0]
df.reset_index(drop=True, inplace=True)
df.isna().sum()
df.tail()


def support(df1, l, n1, n2): #n1 n2 before and after candle l
    for i in range(l-n1+1, l+1):
        if(df1.Low[i]>df1.Low[i-1]):
            return 0
    for i in range(l+1,l+n2+1):
        if(df1.Low[i]<df1.Low[i-1]):
            return 0
    return 1

def resistance(df1, l, n1, n2): #n1 n2 before and after candle l
    for i in range(l-n1+1, l+1):
        if(df1.High[i]<df1.High[i-1]):
            return 0
    for i in range(l+1,l+n2+1):
        if(df1.High[i]>df1.High[i-1]):
            return 0
    return 1


length = len(df)
High = list(df['High'])
Low = list(df['Low'])
Close = list(df['Close'])
Open = list(df['Open'])
bodydiff = [0] * length

highdiff = [0] * length
lowdiff = [0] * length
ratio1 = [0] * length
ratio2 = [0] * length

def isEngulfing(l):
    row=l
    bodydiff[row] = abs(Open[row]-Close[row])
    if bodydiff[row]<0.000001:
        bodydiff[row]=0.000001      

    bodydiffmin = 0.002
    if (bodydiff[row]>bodydiffmin and bodydiff[row-1]>bodydiffmin and
        Open[row-1]<Close[row-1] and
        Open[row]>Close[row] and 
        (Open[row]-Close[row-1])>=-0e-5 and Close[row]<Open[row-1]): #+0e-5 -5e-5
        return 1

    elif(bodydiff[row]>bodydiffmin and bodydiff[row-1]>bodydiffmin and
        Open[row-1]>Close[row-1] and
        Open[row]<Close[row] and 
        (Open[row]-Close[row-1])<=+0e-5 and Close[row]>Open[row-1]):#-0e-5 +5e-5
        return 2
    else:
        return 0
       
def isStar(l):
    bodydiffmin = 0.0020
    row=l
    highdiff[row] = High[row]-max(Open[row],Close[row])
    lowdiff[row] = min(Open[row],Close[row])-Low[row]
    bodydiff[row] = abs(Open[row]-Close[row])
    if bodydiff[row]<0.000001:
        bodydiff[row]=0.000001
    ratio1[row] = highdiff[row]/bodydiff[row]
    ratio2[row] = lowdiff[row]/bodydiff[row]

    if (ratio1[row]>1 and lowdiff[row]<0.2*highdiff[row] and bodydiff[row]>bodydiffmin):# and Open[row]>Close[row]):
        return 1
    elif (ratio2[row]>1 and highdiff[row]<0.2*lowdiff[row] and bodydiff[row]>bodydiffmin):# and Open[row]<Close[row]):
        return 2
    else:
        return 0
    
def closeResistance(l,levels,lim):
    if len(levels)==0:
        return 0
    c1 = abs(df.High[l]-min(levels, key=lambda x:abs(x-df.High[l])))<=lim
    c2 = abs(max(df.Open[l],df.Close[l])-min(levels, key=lambda x:abs(x-df.High[l])))<=lim
    c3 = min(df.Open[l],df.Close[l])<min(levels, key=lambda x:abs(x-df.High[l]))
    c4 = df.Low[l]<min(levels, key=lambda x:abs(x-df.High[l]))
    if( (c1 or c2) and c3 and c4 ):
        return 1
    else:
        return 0
    
def closeSupport(l,levels,lim):
    if len(levels)==0:
        return 0
    c1 = abs(df.Low[l]-min(levels, key=lambda x:abs(x-df.Low[l])))<=lim
    c2 = abs(min(df.Open[l],df.Close[l])-min(levels, key=lambda x:abs(x-df.Low[l])))<=lim
    c3 = max(df.Open[l],df.Close[l])>min(levels, key=lambda x:abs(x-df.Low[l]))
    c4 = df.High[l]>min(levels, key=lambda x:abs(x-df.Low[l]))
    if( (c1 or c2) and c3 and c4 ):
        return 1
    else:
        return 0
    
    
    
n1=2
n2=2
backCandles=30
signal = [0] * length

for row in range(backCandles, len(df)-n2):
    ss = []
    rr = []
    for subrow in range(row-backCandles+n1, row+1):
        if support(df, subrow, n1, n2):
            ss.append(df.Low[subrow])
        if resistance(df, subrow, n1, n2):
            rr.append(df.High[subrow])
    #!!!! parameters
    if ((isEngulfing(row)==1 or isStar(row)==1) and closeResistance(row, rr, 150e-5) ):#and df.RSI[row]<30
        signal[row] = 1
    elif((isEngulfing(row)==2 or isStar(row)==2) and closeSupport(row, ss, 150e-5)):#and df.RSI[row]>70
        signal[row] = 2
    else:
        signal[row] = 0


        
        
        
df['signal']=signal

df[df['signal']==2].count()

df.columns = ['Local time', 'Open', 'High', 'Low', 'Close', 'Volume', 'signal']
df=df.iloc[100:200]
df


def SIGNAL():
    return df.signal


#A new strategy needs to extend Strategy class and override its two abstract methods: init() and next().
#Method init() is invoked before the strategy is run. Within it, one ideally precomputes in efficient, 
#vectorized manner whatever indicators and signals the strategy depends on.
#Method next() is then iteratively called by the Backtest instance, once for each data point (data frame row), 
#simulating the incremental availability of each new full candlestick bar.

#Note, backtesting.py cannot make decisions / trades within candlesticks — any new orders are executed on the
#next candle's open (or the current candle's close if trade_on_close=True). 
#If you find yourself wishing to trade within candlesticks (e.g. daytrading), you instead need to begin 
#with more fine-grained (e.g. hourly) data.


from backtesting import Strategy

class MyCandlesStrat(Strategy):  
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next() 
        if self.signal1==2:
            sl1 = self.data.Close[-1] - 750e-4
            tp1 = self.data.Close[-1] + 600e-4
            self.buy(sl=sl1, tp=tp1)
        elif self.signal1==1:
            sl1 = self.data.Close[-1] + 750e-4
            tp1 = self.data.Close[-1] - 600e-4
            self.sell(sl=sl1, tp=tp1)
            
            
            
from backtesting import Backtest

bt = Backtest(df, MyCandlesStrat, cash=10_000, commission=.002)
stat = bt.run()
stat


bt.plot()


In [23]:
df.columns = ['Local time', 'Open', 'High', 'Low', 'Close', 'Volume', 'signal']
df=df.iloc[100:200]
df

Local time     Open     High      Low    Close   Volume  \
100  30.09.2019 08:20:00.000  1.09352  1.09367  1.09332  1.09353   926.89   
101  30.09.2019 08:25:00.000  1.09353  1.09358  1.09351  1.09356   527.92   
102  30.09.2019 08:30:00.000  1.09356  1.09358  1.09331  1.09338   663.84   
103  30.09.2019 08:35:00.000  1.09338  1.09368  1.09337  1.09358   983.88   
104  30.09.2019 08:40:00.000  1.09358  1.09388  1.09355  1.09380  1145.22   
..                       ...      ...      ...      ...      ...      ...   
195  30.09.2019 16:15:00.000  1.09056  1.09072  1.09047  1.09066   435.49   
196  30.09.2019 16:20:00.000  1.09067  1.09092  1.09057  1.09088   609.38   
197  30.09.2019 16:25:00.000  1.09088  1.09125  1.09087  1.09125   540.62   
198  30.09.2019 16:30:00.000  1.09123  1.09123  1.09107  1.09110   643.47   
199  30.09.2019 16:35:00.000  1.09110  1.09113  1.09067  1.09069   539.70   

     signal  
100       0  
101       0  
102       0  
103       0  
104       0  
..      ...  
195       0  
196       0  
197       0  
198       0  
199       0  

[100 rows x 7 columns]

In [24]:
def SIGNAL():
    return df.signal

In [25]:
#A new strategy needs to extend Strategy class and override its two abstract methods: init() and next().
#Method init() is invoked before the strategy is run. Within it, one ideally precomputes in efficient, 
#vectorized manner whatever indicators and signals the strategy depends on.
#Method next() is then iteratively called by the Backtest instance, once for each data point (data frame row), 
#simulating the incremental availability of each new full candlestick bar.

#Note, backtesting.py cannot make decisions / trades within candlesticks — any new orders are executed on the
#next candle's open (or the current candle's close if trade_on_close=True). 
#If you find yourself wishing to trade within candlesticks (e.g. daytrading), you instead need to begin 
#with more fine-grained (e.g. hourly) data.

In [26]:
from backtesting import Strategy

class MyCandlesStrat(Strategy):  
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next() 
        if self.signal1==2:
            sl1 = self.data.Close[-1] - 750e-4
            tp1 = self.data.Close[-1] + 600e-4
            self.buy(sl=sl1, tp=tp1)
        elif self.signal1==1:
            sl1 = self.data.Close[-1] + 750e-4
            tp1 = self.data.Close[-1] - 600e-4
            self.sell(sl=sl1, tp=tp1)

C:\Users\NOC\anaconda3\lib\site-packages\backtesting\_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

In [27]:
from backtesting import Backtest

bt = Backtest(df, MyCandlesStrat, cash=10_000, commission=.002)
stat = bt.run()
stat



C:\Users\NOC\AppData\Local\Temp/ipykernel_18980/3988754407.py:3: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df, MyCandlesStrat, cash=10_000, commission=.002)


Start                                   100.0
End                                     199.0
Duration                                 99.0
Exposure Time [%]                         0.0
Equity Final [$]                      10000.0
Equity Peak [$]                       10000.0
Return [%]                                0.0
Buy & Hold Return [%]               -0.259709
Return (Ann.) [%]                         0.0
Volatility (Ann.) [%]                     NaN
Sharpe Ratio                              NaN
Sortino Ratio                             NaN
Calmar Ratio                              NaN
Max. Drawdown [%]                        -0.0
Avg. Drawdown [%]                         NaN
Max. Drawdown Duration                    NaN
Avg. Drawdown Duration                    NaN
# Trades                                  0.0
Win Rate [%]                              NaN
Best Trade [%]                            NaN
Worst Trade [%]                           NaN
Avg. Trade [%]                    

In [28]:
bt.plot()

Row(id='1221', ...)

In [29]:
import pandas as pd

# Load the data
df = pd.read_csv("EURUSD_Candlestick_5_M_ASK_30_09_2019_30_09_2022.csv")

# Check if NA values are in data
print("Checking for NA values...")
df = df[df['Volume'] != 0]
df.reset_index(drop=True, inplace=True)
print("NA values check complete. NA count per column:")
print(df.isna().sum())
print("Last 5 rows of the data:")
print(df.tail())

def support(df1, l, n1, n2): # n1 n2 before and after candle l
    for i in range(l - n1 + 1, l + 1):
        if df1.Low[i] > df1.Low[i - 1]:
            return 0
    for i in range(l + 1, l + n2 + 1):
        if df1.Low[i] < df1.Low[i - 1]:
            return 0
    return 1

def resistance(df1, l, n1, n2): # n1 n2 before and after candle l
    for i in range(l - n1 + 1, l + 1):
        if df1.High[i] < df1.High[i - 1]:
            return 0
    for i in range(l + 1, l + n2 + 1):
        if df1.High[i] > df1.High[i - 1]:
            return 0
    return 1

length = len(df)
High = list(df['High'])
Low = list(df['Low'])
Close = list(df['Close'])
Open = list(df['Open'])
bodydiff = [0] * length
highdiff = [0] * length
lowdiff = [0] * length
ratio1 = [0] * length
ratio2 = [0] * length

def isEngulfing(l):
    row = l
    bodydiff[row] = abs(Open[row] - Close[row])
    if bodydiff[row] < 0.000001:
        bodydiff[row] = 0.000001      

    bodydiffmin = 0.002
    if (bodydiff[row] > bodydiffmin and bodydiff[row - 1] > bodydiffmin and
        Open[row - 1] < Close[row - 1] and
        Open[row] > Close[row] and 
        (Open[row] - Close[row - 1]) >= -0e-5 and Close[row] < Open[row - 1]):
        return 1

    elif(bodydiff[row] > bodydiffmin and bodydiff[row - 1] > bodydiffmin and
         Open[row - 1] > Close[row - 1] and
         Open[row] < Close[row] and 
         (Open[row] - Close[row - 1]) <= +0e-5 and Close[row] > Open[row - 1]):
        return 2
    else:
        return 0

def isStar(l):
    bodydiffmin = 0.0020
    row = l
    highdiff[row] = High[row] - max(Open[row], Close[row])
    lowdiff[row] = min(Open[row], Close[row]) - Low[row]
    bodydiff[row] = abs(Open[row] - Close[row])
    if bodydiff[row] < 0.000001:
        bodydiff[row] = 0.000001
    ratio1[row] = highdiff[row] / bodydiff[row]
    ratio2[row] = lowdiff[row] / bodydiff[row]

    if (ratio1[row] > 1 and lowdiff[row] < 0.2 * highdiff[row] and bodydiff[row] > bodydiffmin):
        return 1
    elif (ratio2[row] > 1 and highdiff[row] < 0.2 * lowdiff[row] and bodydiff[row] > bodydiffmin):
        return 2
    else:
        return 0

def closeResistance(l, levels, lim):
    if len(levels) == 0:
        return 0
    c1 = abs(df.High[l] - min(levels, key=lambda x: abs(x - df.High[l]))) <= lim
    c2 = abs(max(df.Open[l], df.Close[l]) - min(levels, key=lambda x: abs(x - df.High[l]))) <= lim
    c3 = min(df.Open[l], df.Close[l]) < min(levels, key=lambda x: abs(x - df.High[l]))
    c4 = df.Low[l] < min(levels, key=lambda x: abs(x - df.High[l]))
    if (c1 or c2) and c3 and c4:
        return 1
    else:
        return 0

def closeSupport(l, levels, lim):
    if len(levels) == 0:
        return 0
    c1 = abs(df.Low[l] - min(levels, key=lambda x: abs(x - df.Low[l]))) <= lim
    c2 = abs(min(df.Open[l], df.Close[l]) - min(levels, key=lambda x: abs(x - df.Low[l]))) <= lim
    c3 = max(df.Open[l], df.Close[l]) > min(levels, key=lambda x: abs(x - df.Low[l]))
    c4 = df.High[l] > min(levels, key=lambda x: abs(x - df.Low[l]))
    if (c1 or c2) and c3 and c4:
        return 1
    else:
        return 0

n1 = 2
n2 = 2
backCandles = 30
signal = [0] * length

print("Starting signal calculation...")
for row in range(backCandles, len(df) - n2):
    ss = []
    rr = []
    for subrow in range(row - backCandles + n1, row + 1):
        if support(df, subrow, n1, n2):
            ss.append(df.Low[subrow])
        if resistance(df, subrow, n1, n2):
            rr.append(df.High[subrow])
    if ((isEngulfing(row) == 1 or isStar(row) == 1) and closeResistance(row, rr, 150e-5)):
        signal[row] = 1
    elif((isEngulfing(row) == 2 or isStar(row) == 2) and closeSupport(row, ss, 150e-5)):
        signal[row] = 2
    else:
        signal[row] = 0

    print(f"Row: {row}, Signal: {signal[row]}")

print("Signal calculation complete.")
df['signal'] = signal

print("Count of signals with value 2:")
print(df[df['signal'] == 2].count())

df.columns = ['Local time', 'Open', 'High', 'Low', 'Close', 'Volume', 'signal']
df = df.iloc[100:200]
print("Filtered DataFrame:")
print(df)

def SIGNAL():
    return df.signal

from backtesting import Strategy

class MyCandlesStrat(Strategy):
    def init(self):
        super().init()
        self.signal1 = self.I(SIGNAL)

    def next(self):
        super().next()
        if self.signal1 == 2:
            sl1 = self.data.Close[-1] - 750e-4
            tp1 = self.data.Close[-1] + 600e-4
            self.buy(sl=sl1, tp=tp1)
        elif self.signal1 == 1:
            sl1 = self.data.Close[-1] + 750e-4
            tp1 = self.data.Close[-1] - 600e-4
            self.sell(sl=sl1, tp=tp1)

from backtesting import Backtest

print("Running backtest...")
bt = Backtest(df, MyCandlesStrat, cash=10_000, commission=.002)
stat = bt.run()
print("Backtest complete.")
print(stat)

bt.plot()


Checking for NA values...
NA values check complete. NA count per column:
Gmt time    0
Open        0
High        0
Low         0
Close       0
Volume      0
dtype: int64
Last 5 rows of the data:
                       Gmt time     Open     High      Low    Close   Volume
225081  30.09.2022 20:35:00.000  0.98028  0.98034  0.98001  0.98022   624.12
225082  30.09.2022 20:40:00.000  0.98023  0.98047  0.98007  0.98030   408.20
225083  30.09.2022 20:45:00.000  0.98026  0.98034  0.98019  0.98031   317.29
225084  30.09.2022 20:50:00.000  0.98031  0.98067  0.97987  0.97999  1472.13
225085  30.09.2022 20:55:00.000  0.98000  0.98066  0.97993  0.98026  1068.81
Starting signal calculation...
Row: 30, Signal: 0
Row: 31, Signal: 0
Row: 32, Signal: 0
Row: 33, Signal: 0
Row: 34, Signal: 0
Row: 35, Signal: 0
Row: 36, Signal: 0
Row: 37, Signal: 0
Row: 38, Signal: 0
Row: 39, Signal: 0
Row: 40, Signal: 0
Row: 41, Signal: 0
Row: 42, Signal: 0
Row: 43, Signal: 0
Row: 44, Signal: 0
Row: 45, Signal: 0
Row: 46,

Row: 408, Signal: 0
Row: 409, Signal: 0
Row: 410, Signal: 0
Row: 411, Signal: 0
Row: 412, Signal: 0
Row: 413, Signal: 0
Row: 414, Signal: 0
Row: 415, Signal: 0
Row: 416, Signal: 0
Row: 417, Signal: 0
Row: 418, Signal: 0
Row: 419, Signal: 0
Row: 420, Signal: 0
Row: 421, Signal: 0
Row: 422, Signal: 0
Row: 423, Signal: 0
Row: 424, Signal: 0
Row: 425, Signal: 0
Row: 426, Signal: 0
Row: 427, Signal: 0
Row: 428, Signal: 0
Row: 429, Signal: 0
Row: 430, Signal: 0
Row: 431, Signal: 0
Row: 432, Signal: 0
Row: 433, Signal: 0
Row: 434, Signal: 0
Row: 435, Signal: 0
Row: 436, Signal: 0
Row: 437, Signal: 0
Row: 438, Signal: 0
Row: 439, Signal: 0
Row: 440, Signal: 0
Row: 441, Signal: 0
Row: 442, Signal: 0
Row: 443, Signal: 0
Row: 444, Signal: 0
Row: 445, Signal: 0
Row: 446, Signal: 0
Row: 447, Signal: 0
Row: 448, Signal: 0
Row: 449, Signal: 0
Row: 450, Signal: 0
Row: 451, Signal: 0
Row: 452, Signal: 0
Row: 453, Signal: 0
Row: 454, Signal: 0
Row: 455, Signal: 0
Row: 456, Signal: 0
Row: 457, Signal: 0


Row: 896, Signal: 0
Row: 897, Signal: 0
Row: 898, Signal: 0
Row: 899, Signal: 0
Row: 900, Signal: 0
Row: 901, Signal: 0
Row: 902, Signal: 0
Row: 903, Signal: 0
Row: 904, Signal: 0
Row: 905, Signal: 0
Row: 906, Signal: 0
Row: 907, Signal: 0
Row: 908, Signal: 0
Row: 909, Signal: 0
Row: 910, Signal: 0
Row: 911, Signal: 0
Row: 912, Signal: 0
Row: 913, Signal: 0
Row: 914, Signal: 0
Row: 915, Signal: 0
Row: 916, Signal: 0
Row: 917, Signal: 0
Row: 918, Signal: 0
Row: 919, Signal: 0
Row: 920, Signal: 0
Row: 921, Signal: 0
Row: 922, Signal: 0
Row: 923, Signal: 0
Row: 924, Signal: 0
Row: 925, Signal: 0
Row: 926, Signal: 0
Row: 927, Signal: 0
Row: 928, Signal: 0
Row: 929, Signal: 0
Row: 930, Signal: 0
Row: 931, Signal: 0
Row: 932, Signal: 0
Row: 933, Signal: 0
Row: 934, Signal: 0
Row: 935, Signal: 0
Row: 936, Signal: 0
Row: 937, Signal: 0
Row: 938, Signal: 0
Row: 939, Signal: 0
Row: 940, Signal: 0
Row: 941, Signal: 0
Row: 942, Signal: 0
Row: 943, Signal: 0
Row: 944, Signal: 0
Row: 945, Signal: 0


Row: 1295, Signal: 0
Row: 1296, Signal: 0
Row: 1297, Signal: 0
Row: 1298, Signal: 0
Row: 1299, Signal: 0
Row: 1300, Signal: 0
Row: 1301, Signal: 0
Row: 1302, Signal: 0
Row: 1303, Signal: 0
Row: 1304, Signal: 0
Row: 1305, Signal: 0
Row: 1306, Signal: 0
Row: 1307, Signal: 0
Row: 1308, Signal: 0
Row: 1309, Signal: 0
Row: 1310, Signal: 0
Row: 1311, Signal: 0
Row: 1312, Signal: 0
Row: 1313, Signal: 0
Row: 1314, Signal: 0
Row: 1315, Signal: 0
Row: 1316, Signal: 0
Row: 1317, Signal: 0
Row: 1318, Signal: 0
Row: 1319, Signal: 0
Row: 1320, Signal: 0
Row: 1321, Signal: 0
Row: 1322, Signal: 0
Row: 1323, Signal: 0
Row: 1324, Signal: 0
Row: 1325, Signal: 0
Row: 1326, Signal: 0
Row: 1327, Signal: 0
Row: 1328, Signal: 0
Row: 1329, Signal: 0
Row: 1330, Signal: 0
Row: 1331, Signal: 0
Row: 1332, Signal: 0
Row: 1333, Signal: 0
Row: 1334, Signal: 0
Row: 1335, Signal: 0
Row: 1336, Signal: 0
Row: 1337, Signal: 0
Row: 1338, Signal: 0
Row: 1339, Signal: 0
Row: 1340, Signal: 0
Row: 1341, Signal: 0
Row: 1342, Si

Row: 1692, Signal: 0
Row: 1693, Signal: 0
Row: 1694, Signal: 0
Row: 1695, Signal: 0
Row: 1696, Signal: 0
Row: 1697, Signal: 0
Row: 1698, Signal: 0
Row: 1699, Signal: 0
Row: 1700, Signal: 0
Row: 1701, Signal: 0
Row: 1702, Signal: 0
Row: 1703, Signal: 0
Row: 1704, Signal: 0
Row: 1705, Signal: 0
Row: 1706, Signal: 0
Row: 1707, Signal: 0
Row: 1708, Signal: 0
Row: 1709, Signal: 0
Row: 1710, Signal: 0
Row: 1711, Signal: 0
Row: 1712, Signal: 0
Row: 1713, Signal: 0
Row: 1714, Signal: 0
Row: 1715, Signal: 0
Row: 1716, Signal: 0
Row: 1717, Signal: 0
Row: 1718, Signal: 0
Row: 1719, Signal: 0
Row: 1720, Signal: 0
Row: 1721, Signal: 0
Row: 1722, Signal: 0
Row: 1723, Signal: 0
Row: 1724, Signal: 0
Row: 1725, Signal: 0
Row: 1726, Signal: 0
Row: 1727, Signal: 0
Row: 1728, Signal: 0
Row: 1729, Signal: 0
Row: 1730, Signal: 0
Row: 1731, Signal: 0
Row: 1732, Signal: 0
Row: 1733, Signal: 0
Row: 1734, Signal: 0
Row: 1735, Signal: 0
Row: 1736, Signal: 0
Row: 1737, Signal: 0
Row: 1738, Signal: 0
Row: 1739, Si

...

Row: 224059, Signal: 0
Row: 224060, Signal: 0
Row: 224061, Signal: 0
Row: 224062, Signal: 0
Row: 224063, Signal: 0
Row: 224064, Signal: 0
Row: 224065, Signal: 0
Row: 224066, Signal: 0
Row: 224067, Signal: 0
Row: 224068, Signal: 0
Row: 224069, Signal: 0
Row: 224070, Signal: 0
Row: 224071, Signal: 0
Row: 224072, Signal: 0
Row: 224073, Signal: 0
Row: 224074, Signal: 0
Row: 224075, Signal: 0
Row: 224076, Signal: 0
Row: 224077, Signal: 0
Row: 224078, Signal: 0
Row: 224079, Signal: 0
Row: 224080, Signal: 0
Row: 224081, Signal: 0
Row: 224082, Signal: 0
Row: 224083, Signal: 0
Row: 224084, Signal: 0
Row: 224085, Signal: 0
Row: 224086, Signal: 0
Row: 224087, Signal: 0
Row: 224088, Signal: 0
Row: 224089, Signal: 0
Row: 224090, Signal: 0
Row: 224091, Signal: 0
Row: 224092, Signal: 0
Row: 224093, Signal: 0
Row: 224094, Signal: 0
Row: 224095, Signal: 0
Row: 224096, Signal: 0
Row: 224097, Signal: 0
Row: 224098, Signal: 0
Row: 224099, Signal: 0
Row: 224100, Signal: 0
Row: 224101, Signal: 0
Row: 224102

Row: 224416, Signal: 0
Row: 224417, Signal: 0
Row: 224418, Signal: 0
Row: 224419, Signal: 0
Row: 224420, Signal: 0
Row: 224421, Signal: 0
Row: 224422, Signal: 0
Row: 224423, Signal: 0
Row: 224424, Signal: 0
Row: 224425, Signal: 0
Row: 224426, Signal: 0
Row: 224427, Signal: 0
Row: 224428, Signal: 0
Row: 224429, Signal: 0
Row: 224430, Signal: 0
Row: 224431, Signal: 0
Row: 224432, Signal: 0
Row: 224433, Signal: 0
Row: 224434, Signal: 0
Row: 224435, Signal: 0
Row: 224436, Signal: 0
Row: 224437, Signal: 0
Row: 224438, Signal: 0
Row: 224439, Signal: 0
Row: 224440, Signal: 0
Row: 224441, Signal: 0
Row: 224442, Signal: 0
Row: 224443, Signal: 0
Row: 224444, Signal: 0
Row: 224445, Signal: 0
Row: 224446, Signal: 0
Row: 224447, Signal: 0
Row: 224448, Signal: 0
Row: 224449, Signal: 0
Row: 224450, Signal: 0
Row: 224451, Signal: 0
Row: 224452, Signal: 0
Row: 224453, Signal: 0
Row: 224454, Signal: 0
Row: 224455, Signal: 0
Row: 224456, Signal: 0
Row: 224457, Signal: 0
Row: 224458, Signal: 0
Row: 224459

Row: 224781, Signal: 0
Row: 224782, Signal: 0
Row: 224783, Signal: 0
Row: 224784, Signal: 0
Row: 224785, Signal: 0
Row: 224786, Signal: 0
Row: 224787, Signal: 0
Row: 224788, Signal: 0
Row: 224789, Signal: 0
Row: 224790, Signal: 0
Row: 224791, Signal: 0
Row: 224792, Signal: 0
Row: 224793, Signal: 0
Row: 224794, Signal: 0
Row: 224795, Signal: 0
Row: 224796, Signal: 0
Row: 224797, Signal: 0
Row: 224798, Signal: 0
Row: 224799, Signal: 0
Row: 224800, Signal: 0
Row: 224801, Signal: 0
Row: 224802, Signal: 0
Row: 224803, Signal: 0
Row: 224804, Signal: 0
Row: 224805, Signal: 0
Row: 224806, Signal: 0
Row: 224807, Signal: 0
Row: 224808, Signal: 0
Row: 224809, Signal: 0
Row: 224810, Signal: 0
Row: 224811, Signal: 0
Row: 224812, Signal: 0
Row: 224813, Signal: 0
Row: 224814, Signal: 0
Row: 224815, Signal: 0
Row: 224816, Signal: 0
Row: 224817, Signal: 0
Row: 224818, Signal: 0
Row: 224819, Signal: 0
Row: 224820, Signal: 0
Row: 224821, Signal: 0
Row: 224822, Signal: 0
Row: 224823, Signal: 0
Row: 224824

C:\Users\NOC\AppData\Local\Temp/ipykernel_18980/900198324.py:165: UserWarning: Data index is not datetime. Assuming simple periods, but `pd.DateTimeIndex` is advised.
  bt = Backtest(df, MyCandlesStrat, cash=10_000, commission=.002)


Row(id='1616', ...)